![](images/EscUpmPolit_p.gif "UPM")

# Course Notes for Learning Intelligent Systems

Department of Telematic Engineering Systems, Universidad Politécnica de Madrid, © 2016 Carlos A. Iglesias

# Syntactic Processing

# Table of Contents

* [Objectives](#Objectives)
* [POS Tagging](#POS-Tagging)
* [NER](#NER)
* [Parsing and Chunking](#Parsing-and-Chunking)

# Objectives

In this session we are going to learn how to analyse the syntax of text. In particular, we will learn
* Understand and perform POS (Part of Speech) tagging
* Understand and perform NER (Named Entity Recognition)
* Understand and parse texts

We will use the same examples than in the previous notebook, slightly modified for learning purposes.

In [ ]:
review = """I purchased this Dell monitor because of budgetary concerns. This item was the most inexpensive 17 inch Apple monitor 
available to me at the time I made the purchase. My overall experience with this monitor was very poor. When the 
screen  wasn't contracting or glitching the overall picture quality was poor to fair. I've viewed numerous different 
monitor models since I 'm a college student at UPM in Madrid and this particular monitor had as poor of picture quality as 
any I 've seen."""

tweet = """@concert Lady Gaga is actually at the Britney Spears Femme Fatale Concert tonight!!! She still listens to 
        her music!!!! WOW!!! #ladygaga #britney"""

# POS Tagging

POS Tagging is the process of assigning a grammatical category (known as *part of speech*, POS) to a word. For this purpose, the most common approach is using an annotated corpus such as Penn Treebank. The tag set (categories) depends on the corpus annotation. Fortunately, nltk defines a [universal tagset](http://www.nltk.org/book/ch05.html):


Tag	| Meaning | English Examples
----|---------|------------------
ADJ	| adjective | new, good, high, special, big, local
ADP	| adposition | on, of, at, with, by, into, under
ADV	| adverb | really, already, still, early, now
CONJ| conjunction | and, or, but, if, while, although
DET | determiner, article | the, a, some, most, every, no, which
NOUN | noun	 | year, home, costs, time, Africa
NUM	| numeral | twenty-four, fourth, 1991, 14:24
PRT | particle | at, on, out, over per, that, up, with
PRON | pronoun | he, their, her, its, my, I, us
VERB | verb	| is, say, told, given, playing, would
. | punctuation marks | . , ; !
X | other | ersatz, esprit, dunno, gr8, univeristy

In [ ]:
from nltk import pos_tag, word_tokenize
print (pos_tag(word_tokenize(review), tagset='universal'))

We could have used another tagset for POS, such as UPenn.

In [ ]:
print (pos_tag(word_tokenize(review)))

The meaning of these tags can be obtained here:

In [ ]:
import nltk
nltk.help.upenn_tagset()

We are going to use the Univeral tagset in this example. Based on this POS info, we could use correctly now the WordNetLemmatizer. The WordNetLemmatizer only is interesting for 4 POS categories: ADJ, ADV, NOUN, and VERB. This is because WordNet lemmatizer will only lemmatize adjectives, adverbs, nouns and verbs, and it needs that all the provided tags are in [n, a, r, v].

In [ ]:
from nltk.stem import WordNetLemmatizer

review_postagged = pos_tag(word_tokenize(review), tagset='universal')
pos_mapping = {'NOUN': 'n', 'ADJ': 'a', 'VERB': 'v', 'ADV': 'r', 'ADP': 'n', 'CONJ': 'n', 
               'PRON': 'n', 'NUM': 'n', 'X': 'n' }

wordnet = WordNetLemmatizer()
lemmas = [wordnet.lemmatize(w, pos=pos_mapping[tag]) for (w,tag)  in review_postagged if tag in pos_mapping.keys()]
print(lemmas)

# NER

Named Entity Recognition (NER) is an information retrieval for identifying named entities of places, organisation of persons. NER usually relies in a tagged corpus. NER algorithms can be trained for new corpora. Here we are using the Brown tagset (http://www.comp.leeds.ac.uk/ccalas/tagsets/brown.html).

In [ ]:
from nltk import ne_chunk, pos_tag, word_tokenize
ne_tagged = ne_chunk(pos_tag(word_tokenize(review)), binary=False)
print(ne_tagged)    

NLTK comes with other NER implementations. We can also use online services, such as [OpenCalais](http://www.opencalais.com/), [DBpedia Spotlight](https://github.com/dbpedia-spotlight/dbpedia-spotlight/wiki/Web-service) or [TagME](http://tagme.di.unipi.it/).

# Parsing and Chunking

**Parsing** is the process of obtaining a parsing tree given a grammar. It which can be very useful to understand the relationship among the words.

As we have seen in class, we can follow a traditional approach and obtain a full parsing tree or shallow parsing (chunking) and obtain a partial tree.

We can use the StandfordParser that is integrated in NLTK, but it requires to configure the CLASSPATH, which can be a bit annoying. Instead, we are going to see some demos to understand how grammars work. In case you are interested, you can consult the [manual](http://www.nltk.org/api/nltk.parse.html) to run it.

In the following example, you will run an interactive context-free parser, called [shift-reduce parser](http://www.nltk.org/book/ch08.html).
The panel on the left shows the grammar as a list of production rules. The panel on the right contains the stack  and the remaining input.

You should:
* Run pressing 'step' until the sentence is fully analyzed. With each step, the parser either shifts one word onto the stack or reduces two subtrees of the stack into a new subtree.
* Try to act as the parser. Instead of pressing 'step', press  'shift' and 'reduce'. Follow the 'always shift before reduce' rule. It is likely you will reach a state where the parser cannot proceed. You can go back with 'Undo'.

In [ ]:
from nltk.app import srparser_app
srparser_app.app()

**Chunking** o **shallow parsing** aims at extracting relevant parts of the sentence. There are (two main approaches)[http://www.nltk.org/book/ch07.html] to chunking: using regular expressions based on POS tags, or training a chunk parser.

We are going to illustrate the first technique for extracting NP chunks.

We define regular expressions for the chunks we want to get.

In [ ]:
from nltk.chunk.regexp import *
pattern = """NP: {<PRON><ADJ><NOUN>+} 
                 {<DET>?<ADV>?<ADJ|NUM>*?<NOUN>+}
                 """
NPChunker = RegexpParser(pattern)

reviews_pos = (pos_tag(word_tokenize(review),  tagset='universal'))

chunks_np = NPChunker.parse(reviews_pos)
print(chunks_np)
chunks_np.draw()

Now we can traverse the trees and obtain the strings as follows.

In [ ]:
def extractTrees(parsed_tree, category='NP'):
    return list(parsed_tree.subtrees(filter=lambda x: x.label()==category))

extractTrees(chunks_np, 'NP')

In [ ]:
def extractStrings(parsed_tree, category='NP'):
    return [" ".join(word for word, pos in vp.leaves()) for vp in extractTrees(parsed_tree, category)]
    
extractStrings(chunks_np)

## References



* [NLTK Book. Natural Language Processing with Python. Steven Bird, Ewan Klein, and Edward Loper. O'Reilly Media, 2009 ](http://www.nltk.org/book_1ed/)
* [NLTK Essentials, Nitin Hardeniya, Packt Publishing, 2015](http://proquest.safaribooksonline.com/search?q=NLTK%20Essentials)

## Licence

The notebook is freely licensed under under the [Creative Commons Attribution Share-Alike license](https://creativecommons.org/licenses/by/2.0/).  

© 2016 Carlos A. Iglesias, Universidad Politécnica de Madrid.